A. Thông tin định danh & Quản lý (Metadata)

job_id: ID duy nhất của tin tuyển dụng trên trang gốc (để tránh crawl trùng).

url: Link chi tiết của bài đăng.

crawl_at: Thời gian bạn thực hiện crawl (dùng để theo dõi độ tươi của dữ liệu).

posted_at: Ngày đăng tin hoặc ngày cập nhật của nhà tuyển dụng.

B. Nội dung công việc (Job Details)

job_title: Tiêu đề công việc (ví dụ: Senior Java Developer).

job_level: Cấp bậc (Intern, Junior, Senior, Manager...).


min: Mức lương tối thiểu.

max: Mức lương tối đa.


skills: Mảng các kỹ năng (ví dụ: ["Python", "AWS", "ReactJS"]). Đây là trường quan trọng nhất để filter.


## Tiền xử lý ban đầu

In [3]:
import re
import time
import random
from datetime import datetime, timedelta
def convert_to_million(value_str, currency_type):
    try:
        value = float(value_str)
        if currency_type == "usd":
            return round((value * 25400) / 1000000, 2)
        return round(value, 2)
    except:
        return float('nan')

def process_job_data(raw_jobs):
    processed_list = []
    today = datetime.now()
    benefit_keywords = ['thưởng', 'nghỉ', 'bảo hiểm', 'du lịch', 'phụ cấp', 'trưa', 'máy tính', 'lương tháng 13', 'teambuilding', 'chăm sóc']

    for raw in raw_jobs:
        # Xử lý thời gian
        relative_text = raw['posted_at'].lower()
        num_in_time = re.search(r'\d+', relative_text)
        number = int(num_in_time.group()) if num_in_time else 0
        if any(unit in relative_text for unit in ["giờ", "phút", "vừa xong"]):
            exact_date = today
        elif "ngày" in relative_text:
            exact_date = today - timedelta(days=number)
        elif "tuần" in relative_text:
            exact_date = today - timedelta(weeks=number)
        elif "tháng" in relative_text:
            exact_date = today - timedelta(days=number * 30)
        else:
            exact_date = today

        # Xử lý lương
        salary_raw = raw['salary'].upper()
        min_salary = float('nan')
        max_salary = float('nan')
        currency_type = "usd" if "USD" in salary_raw else "vnd"
        clean_salary_text = salary_raw.replace('.', '').replace(',', '')
        numbers = re.findall(r'\d+', clean_salary_text)

        if "THỎA THUẬN" in salary_raw or not numbers:
            pass 
        elif "TỪ" in salary_raw and len(numbers) == 1:
            min_salary = convert_to_million(numbers[0], currency_type)
        elif any(x in salary_raw for x in ["TỚI", "ĐẾN", "LÊN ĐẾN"]) and len(numbers) == 1:
            max_salary = convert_to_million(numbers[0], currency_type)
        elif len(numbers) >= 2:
            min_salary = convert_to_million(numbers[0], currency_type)
            max_salary = convert_to_million(numbers[1], currency_type)
        elif len(numbers) == 1:
            min_salary = convert_to_million(numbers[0], currency_type)

        # Phân loại tags
        skills = []
        benefits = []
        for tag in raw['skills']:
            if any(kw in tag.lower() for kw in benefit_keywords):
                benefits.append(tag)
            else:
                skills.append(tag)

        processed_list.append({
            "job_id": raw['job_id'],
            "title": raw['title'],
            "company": raw['company'],
            "url": raw['url'],
            "salary_raw": raw['salary'],
            "min_salary_mil": min_salary,
            "max_salary_mil": max_salary,
            "skills": skills,
            "benefits": benefits,
            "posted_date": exact_date.strftime('%Y-%m-%d'),
            "processed_at": today.strftime('%Y-%m-%d %H:%M:%S')
        })
    return processed_list

if __name__ == "__main__":
    processed_data = process_job_data(results)
    
    # 3. Hiển thị kết quả
    print("\nKẾT QUẢ SAU XỬ LÝ:")
    for job in processed_data:
        print(f"--- {job['title']} ---")
        print(f"Công ty: {job['company']}")
        print(f"Lương Min: {job['min_salary_mil']}tr | Max: {job['max_salary_mil']}tr")
        print(f"Kỹ năng: {job['skills']}")
        print(f"Ngày đăng: {job['posted_date']}")


KẾT QUẢ SAU XỬ LÝ:
--- Nhân Viên Kinh Doanh / Hỗ Trợ Bán Hàng Tại Văn Phòng Quận 12 ( Data Có Sẵn - Thử Việc 100% Lương - Thu Nhập 10-20 Triệu/Tháng) ---
Công ty: Công ty TNHH Vietnam Concentrix Services
Lương Min: nantr | Max: 20.0tr
Kỹ năng: ['Call Center/Trực tổng đài', 'Bán lẻ - Hàng t...']
Ngày đăng: 2025-12-16
--- Chuyên Viên Tư Vấn /Chốt Đơn Khóa Học - Lương Cứng 11-17 Triệu + Hoa Hồng (Thu Nhập Upto 30 Triệu/Tháng) - Yêu Cầu Tối Thiểu 1 Năm Kinh Nghiệm Telesale/Sale - Data Sẵn 100% ---
Công ty: EDUPIA
Lương Min: nantr | Max: 30.0tr
Kỹ năng: ['Tư vấn tuyển sinh/khoá học', 'Telesales', 'B2C', 'Y ...']
Ngày đăng: 2025-12-22
--- Cộng Tác Viên Tư Vấn Tài Chính - Không Áp Doanh Số/Linh Hoạt Thời Gian (Miền Bắc) ---
Công ty: FE CREDIT
Lương Min: 12.0tr | Max: 15.0tr
Kỹ năng: ['Tư vấn tài chính', 'B2B', 'Tài chính', 'Bưu chính', 'Bất...']
Ngày đăng: 2025-12-19
--- Kế Toán Tổng Hợp ---
Công ty: CÔNG TY CỔ PHẦN CƠ KHÍ CÔNG MINH
Lương Min: nantr | Max: nantr
Kỹ năng: ['Kế toán tổng hợp',

## Code Crawl

In [1]:
import time
import random
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from webdriver_manager.chrome import ChromeDriverManager

def get_driver():
    options = Options()
    # options.add_argument("--headless") 
    options.add_argument("window-size=1920,1080")
    options.add_argument("--disable-blink-features=AutomationControlled")
    options.add_experimental_option("excludeSwitches", ["enable-automation"])
    options.add_experimental_option('useAutomationExtension', False)
    
    user_agents = [
        "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/119.0.0.0 Safari/537.36",
        "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/118.0.0.0 Safari/537.36"
    ]
    options.add_argument(f"user-agent={random.choice(user_agents)}")
    
    driver = webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)
    driver.execute_script("Object.defineProperty(navigator, 'webdriver', {get: () => undefined})")
    return driver

def scroll_down(driver):
    total_height = int(driver.execute_script("return document.body.scrollHeight"))
    for i in range(1, total_height, 400):
        driver.execute_script(f"window.scrollTo(0, {i});")
        time.sleep(0.1)

def extract_page_data(html):
    """Xử lý HTML bằng BeautifulSoup"""
    soup = BeautifulSoup(html, 'html.parser')
    job_items = soup.select('.job-item-search-result')
    
    page_data = []
    for item in job_items:
        # Lấy ID từ attribute data-job-id
        job_id = item.get('data-job-id')
        
        # Lấy tiêu đề và Link
        title_tag = item.select_one('h3.title a')
        job_title = title_tag.get_text(strip=True) if title_tag else "N/A"
        job_url = title_tag.get('href').split('?')[0] if title_tag else "N/A"
        
        # Lấy tên công ty
        company_tag = item.select_one('.company-name, .company a')
        company_name = company_tag.get_text(strip=True) if company_tag else "N/A"
        
        # Lấy mức lương
        salary_tag = item.select_one('.title-salary, .salary')
        salary = salary_tag.get_text(strip=True) if salary_tag else "Thỏa thuận"
        
        # Lấy địa điểm (city-text)
        location_tag = item.select_one('.city-text')
        location = location_tag.get_text(strip=True) if location_tag else "N/A"

        # Lấy kinh nghiệm (exp)
        exp_tag = item.select_one('.exp span')
        experience = exp_tag.get_text(strip=True) if exp_tag else "Không yêu cầu"
        
        #  LẤY SKILLS (TAGS) ---
        # TopCV hiển thị tags trong class .tag, mỗi tag là một .item-tag
        tag_elements = item.select('.tag .item-tag')
        skills = [tag.get_text(strip=True) for tag in tag_elements]
        
        time_tag = item.select_one('.label-update')
        posted_at = time_tag.get_text(strip=True).replace("Đăng ", "") if time_tag else "N/A"

        page_data.append({
            "job_id": job_id,
            "title": job_title,
            "url": job_url,
            "company": company_name,
            "salary": salary,
            "location": location,
            "exp": experience,
            "skills": skills,  
            "posted_at": posted_at
        })
    return page_data

def start_crawl(url):
    driver = get_driver()
    driver.get(url)
    
    all_jobs = []
    page_num = 1

    try:
        while True:
            print(f"\n--- Đang cào trang {page_num} ---")
            
            # Đợi danh sách việc làm xuất hiện
            WebDriverWait(driver, 10).until(
                EC.presence_of_element_located((By.CLASS_NAME, "job-item-search-result"))
            )
            # Cuộn xuống để đảm bảo mọi thứ được load
            scroll_down(driver)
            time.sleep(1)
            # Trích xuất dữ liệu
            jobs = extract_page_data(driver.page_source)
            for j in jobs:
                print(f"[{j['job_id']}] {j['title']} | Skills: {', '.join(j['skills'][:3])}...")
            
            all_jobs.extend(jobs)
            # Tìm nút Next
            try:
                next_btn = driver.find_element(By.CSS_SELECTOR, "ul.pagination li a[rel='next']")
                # Cuộn tới nút Next để click
                driver.execute_script("arguments[0].scrollIntoView({block: 'center'});", next_btn)
                time.sleep(1)
                next_btn.click()
                page_num += 1
                # Nghỉ ngẫu nhiên để tránh bot detection
                time.sleep(random.uniform(2, 4))
            except:
                print("\n>>> Đã hết trang hoặc không tìm thấy nút Next.")
                break
                
    finally:
        driver.quit()
        print(f"\nTổng cộng đã cào được {len(all_jobs)} việc làm.")
        return all_jobs

if __name__ == "__main__":
    search_url = "https://www.topcv.vn/tim-viec-lam-kinh-doanh-ban-hang-cr1?type_keyword=1&sba=1&category_family=r1-r92-r158-r177-r206-r257-r333-r392-r417-r477-r544-r612-r644-r711-r750-r781-r826-r857-r883-r899-r1010-r1013-r1014-r1042-r1080&saturday_status=0"
    results = start_crawl(search_url)

<>:129: SyntaxWarning: 'return' in a 'finally' block
C:\Users\Admin\AppData\Local\Temp\ipykernel_55064\3895789062.py:129: SyntaxWarning: 'return' in a 'finally' block
  return all_jobs
C:\Users\Admin\AppData\Local\Temp\ipykernel_55064\3895789062.py:129: SyntaxWarning: 'return' in a 'finally' block
  return all_jobs



--- Đang cào trang 1 ---
[1982399] Nhân Viên Kinh Doanh / Hỗ Trợ Bán Hàng Tại Văn Phòng Quận 12 ( Data Có Sẵn - Thử Việc 100% Lương - Thu Nhập 10-20 Triệu/Tháng) | Skills: Call Center/Trực tổng đài, Bán lẻ - Hàng t......
[1991925] Chuyên Viên Tư Vấn /Chốt Đơn Khóa Học - Lương Cứng 11-17 Triệu + Hoa Hồng (Thu Nhập Upto 30 Triệu/Tháng) - Yêu Cầu Tối Thiểu 1 Năm Kinh Nghiệm Telesale/Sale - Data Sẵn 100% | Skills: Tư vấn tuyển sinh/khoá học, Telesales, B2C...
[1549646] Cộng Tác Viên Tư Vấn Tài Chính - Không Áp Doanh Số/Linh Hoạt Thời Gian (Miền Bắc) | Skills: Tư vấn tài chính, B2B, Tài chính...
[1950261] Kế Toán Tổng Hợp | Skills: Kế toán tổng hợp, 5 năm kinh nghiệm, Cao Đẳn......
[1980167] Trưởng Phòng Kinh Doanh Bất Động Sản - 2 Năm Kinh Nghiệm Trở Lên (Thu Nhập Từ 30 Triệu Trở Lên) | Skills: Sales bất động sản/Môi giới bất động sản...
[1986484] Vacation Consultant/ Nhân Viên Tư Vấn Du Lịch, Kỳ Nghỉ (Lương Cứng Từ 10 - 20 Triệu + Hoa Hồng + Thưởng Nóng) | Skills: Sales Tour/Kinh doanh d

## In một số kết quả

In [12]:
results[0]

{'job_id': '1982399',
 'title': 'Nhân Viên Kinh Doanh / Hỗ Trợ Bán Hàng Tại Văn Phòng Quận 12 ( Data Có Sẵn - Thử Việc 100% Lương - Thu Nhập 10-20 Triệu/Tháng)',
 'url': 'https://www.topcv.vn/brand/concentrixservices/tuyen-dung/nhan-vien-kinh-doanh-ho-tro-ban-hang-tai-van-phong-quan-12-data-co-san-thu-viec-100-luong-thu-nhap-10-20-trieu-thang-j1982399.html',
 'company': 'Công ty TNHH Vietnam Concentrix Services',
 'salary': 'Tới 20 triệu',
 'location': 'Hồ Chí Minh (mới)',
 'exp': 'Dưới 1 năm',
 'skills': ['Call Center/Trực tổng đài', 'Bán lẻ - Hàng t...'],
 'posted_at': 'Đăng1 tuần trước'}

In [13]:
processed_data[0]

{'job_id': '1982399',
 'title': 'Nhân Viên Kinh Doanh / Hỗ Trợ Bán Hàng Tại Văn Phòng Quận 12 ( Data Có Sẵn - Thử Việc 100% Lương - Thu Nhập 10-20 Triệu/Tháng)',
 'company': 'Công ty TNHH Vietnam Concentrix Services',
 'url': 'https://www.topcv.vn/brand/concentrixservices/tuyen-dung/nhan-vien-kinh-doanh-ho-tro-ban-hang-tai-van-phong-quan-12-data-co-san-thu-viec-100-luong-thu-nhap-10-20-trieu-thang-j1982399.html',
 'salary_raw': 'Tới 20 triệu',
 'min_salary_mil': nan,
 'max_salary_mil': 20.0,
 'skills': ['Call Center/Trực tổng đài', 'Bán lẻ - Hàng t...'],
 'benefits': [],
 'posted_date': '2025-12-16',
 'processed_at': '2025-12-23 13:11:26'}

In [5]:
import pandas as pd
# 3. Xuất ra file CSV
df = pd.DataFrame(processed_data)
file_name = f"topcv_jobs_{datetime.now().strftime('%Y%m%d_%H%M%S')}.csv"
        
 # Sử dụng encoding 'utf-8-sig' để Excel không bị lỗi font tiếng Việt
df.to_csv(file_name, index=False, encoding='utf-8-sig')
        
print(f"\n--- THÀNH CÔNG ---")
print(f"Đã lưu dữ liệu vào file: {file_name}")
print(df.head()) # Hiển thị 5 dòng đầu tiên xem thử


--- THÀNH CÔNG ---
Đã lưu dữ liệu vào file: topcv_jobs_20251223_131128.csv
    job_id                                              title  \
0  1982399  Nhân Viên Kinh Doanh / Hỗ Trợ Bán Hàng Tại Văn...   
1  1991925  Chuyên Viên Tư Vấn /Chốt Đơn Khóa Học - Lương ...   
2  1549646  Cộng Tác Viên Tư Vấn Tài Chính - Không Áp Doan...   
3  1950261                                   Kế Toán Tổng Hợp   
4  1980167  Trưởng Phòng Kinh Doanh Bất Động Sản - 2 Năm K...   

                                    company  \
0  Công ty TNHH Vietnam Concentrix Services   
1                                    EDUPIA   
2                                 FE CREDIT   
3          CÔNG TY CỔ PHẦN CƠ KHÍ CÔNG MINH   
4                   CÔNG TY TNHH HEERA & CO   

                                                 url      salary_raw  \
0  https://www.topcv.vn/brand/concentrixservices/...    Tới 20 triệu   
1  https://www.topcv.vn/brand/educa/tuyen-dung/ch...    Tới 30 triệu   
2  https://www.topcv.vn/brand/fecr

In [9]:
df.to_excel('topcv.xlsx', index=False)

In [11]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10000 entries, 0 to 9999
Data columns (total 11 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   job_id          10000 non-null  object 
 1   title           10000 non-null  object 
 2   company         10000 non-null  object 
 3   url             10000 non-null  object 
 4   salary_raw      10000 non-null  object 
 5   min_salary_mil  6532 non-null   float64
 6   max_salary_mil  6452 non-null   float64
 7   skills          10000 non-null  object 
 8   benefits        10000 non-null  object 
 9   posted_date     10000 non-null  object 
 10  processed_at    10000 non-null  object 
dtypes: float64(2), object(9)
memory usage: 859.5+ KB
